In [2]:
from bs4 import BeautifulSoup
import requests
#import bs4
import lxml
from requests.adapters import HTTPAdapter
from urllib3.util.retry import Retry
import pandas as pd
import numpy as np
import re

In [4]:
url_booking = 'https://www.tripadvisor.com.ph/Attractions-g294245-Activities-oa0-Philippines.html'
headers_booking = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/109.0.0.0 Safari/537.36',
    'Accept-Language': 'en-US,en;q=0.9'
}

response_booking  = requests.get(url_booking, headers=headers_booking)

In [5]:
soup_booking = BeautifulSoup(response_booking.text, 'html.parser')
#print(soup_booking)

In [6]:
tourists_name_booking = soup_booking.select('div', {'class': 'hZuqH'})
tourists_name_booking

[<div id="lithium-root"><!--$--><!--$--><!--/$--><div class="CvDIt _Q f e Gi Ra _s P6 Za"><button class="UikNM _G B- _S _T c G_ y wSSLS wnNQG" tabindex="1" type="button"><span class="biGQs _P XWJSj Wb">Skip to main content</span></button></div><div class="ad gKBHA _h Gi f e j u"><div class="UgVGx w KcVpg o" id="slot:5x1-728x90:horizon"></div></div><header class="tfxmn Cj"><div class="QvCXh mvTrV cyIij fluiI"><nav class="pmElb"><button aria-label="Menu" class="ryZJf u j _T _S S8 H0 c Cl _G G_ B- M0 y" title="Menu"><svg class="d Vb UmNoP" height="1em" viewbox="0 0 24 24" width="1em"><path clip-rule="evenodd" d="M21 7.75H3v-1.5h18v1.5zm0 5H3v-1.5h18v1.5zm0 5H3v-1.5h18v1.5z" fill-rule="evenodd"></path></svg></button><a class="pBcSw F0 wSSLS" href="/"><picture><img alt="Tripadvisor" class="BMuGb" src="https://static.tacdn.com/img2/brand_refresh/Tripadvisor_logoset_solid_green.svg"/></picture><picture><img alt="Tripadvisor" class="XpHHt" src="https://static.tacdn.com/img2/brand_refresh/Tripa

In [7]:
tourists_data_booking = []
# Loop over the hotel elements and extract the desired data
for tourist_booking in tourists_name_booking:
    # Extract the name
    tourist_name_booking_element = tourist_booking.select_one('div', {'class': 'XfVdV o AIbhI'})
    tourist_name_booking = None
    if tourist_name_booking_element:
        tourist_name_booking = tourist_name_booking_element.text.strip()

    # Extract the location
    tourist_location_booking_element = tourist_booking.select_one('div', {'class': 'XfVdV o AIbhI' })
    tourist_location_booking = None
    if tourist_location_booking_element:
        tourist_location_booking = tourist_location_booking_element.text.strip()  
    #svg={'class': 'UctUV d H0'}, UctUV d H0 hzzSG
    # Extract the hotel review score
    css_selector = 'svg.UctUV.d.H0.hzzSG[aria-label]'
    tourist_reviewscore_booking_element = tourist_booking.select_one(css_selector)
    tourist_reviewscore_booking = None
    if tourist_reviewscore_booking_element:
        tourist_reviewscore_booking = tourist_reviewscore_booking_element.text.strip()
    if tourist_reviewscore_booking_element:
        # Get the value of the aria-label attribute
        aria_label = tourist_reviewscore_booking_element["aria-label"]
        #print("aria-label:", aria_label)
        tourist_reviewscore_booking = aria_label
    #else:
        #print("Element with aria-label attribute not found.")
    
    # Extract the hotel review feedback
    tourist_reviewfeedback_booking_element = tourist_booking.find('a', {'class': 'BMQDV _F Gv wSSLS SwZTJ FGwzt ukgoS', 'tabindex': '0'})
    tourist_reviewfeedback_booking = None
    if tourist_reviewfeedback_booking_element:
        tourist_reviewfeedback_booking = tourist_reviewfeedback_booking_element.text.strip()
    
    # Extract the hotel review count
    tourist_reviewcount_booking_element = tourist_booking.find('span', {'class': 'biGQs _P pZUbB osNWb'})
    tourist_reviewcount_booking = None
    if tourist_reviewcount_booking_element:
        tourist_reviewcount_booking = tourist_reviewcount_booking_element.text.strip()
    
    # Extract the open
    tourist_category_booking_element = tourist_booking.find('div', {'class': 'biGQs _P pZUbB hmDzD'})
    tourist_category_booking = None
    if tourist_category_booking_element:
        tourist_category_booking = tourist_category_booking_element.text.strip()
    
    # Extract the menu
    tourist_customer_booking_element = tourist_booking.select_one('a', {'class': 'BMQDV _F Gv wSSLS SwZTJ FGwzt ukgoS'})
    tourist_customer_booking = None
    if tourist_customer_booking_element:
        tourist_customer_booking = tourist_customer_booking_element.text.strip()

    # Append hotes_data with info about hotel
    tourists_data_booking.append({
        'Tourist_Spot_Name': tourist_name_booking,
        'Tourist_Spot_Location': tourist_location_booking,
        'Tourist_Spot_Category': tourist_category_booking,
        'Tourist_Spot_Review_Score': tourist_reviewscore_booking,
        #'Tourist_Spot_Customer': tourist_customer_booking,
        #'Tourist_Spot_Review_Feedback': tourist_reviewfeedback_booking,
        'Tourist_Spot_Review_Count': tourist_reviewcount_booking      
    })

In [8]:
# Define a function to extract the formatted text
def format_text(text):
    # Use regular expressions to match and extract the desired part
    match = re.match(r'^(\d+\.\s[^\d]+)', text)
    if match:
        return match.group(1)
    return ''

In [9]:
#List to dataframe and Data Cleaning
tourists_booking = pd.DataFrame(tourists_data_booking)
tourists_booking = tourists_booking.dropna()
tourists_booking.drop(tourists_booking[tourists_booking['Tourist_Spot_Name'] == ''].index, inplace=True)
tourists_booking.drop(tourists_booking[tourists_booking['Tourist_Spot_Location'] == ''].index, inplace=True)
tourists_booking = tourists_booking.drop_duplicates()
#tourists_booking['Tourist_Spot_Name'] = tourists_booking['Tourist_Spot_Name'].str.replace(r'^\d+\.\s', '', regex=True)
tourists_booking['Tourist_Spot_Review_Score'] = tourists_booking['Tourist_Spot_Review_Score'].str.replace(" of 5 bubbles", "").astype(float)
#tourists_booking['Tourist_Spot_Review_Count'] = tourists_booking['Tourist_Spot_Review_Count'].str.replace(" reviews", "")
tourists_booking['Tourist_Spot_Review_Count'] = tourists_booking['Tourist_Spot_Review_Count'].str.replace(",", "").astype(int)
patterns_to_remove = ['2023', '20232.', '20233.', '20234.']
mask = ~tourists_booking['Tourist_Spot_Name'].str.contains('|'.join(map(re.escape, patterns_to_remove)))
tourists_booking = tourists_booking[mask]
pattern = r'\d'
mask = tourists_booking['Tourist_Spot_Name'].str.contains(pattern, na=False)
tourists_booking = tourists_booking[mask]
tourists_booking = tourists_booking.drop(17)
tourists_booking = tourists_booking.drop(294)
tourists_booking['Tourist_Spot_Name'] = tourists_booking['Tourist_Spot_Name'].apply(format_text)
tourists_booking['Tourist_Spot_Location'] = tourists_booking['Tourist_Spot_Location'].apply(format_text)
tourists_booking = tourists_booking.drop_duplicates()
tourists_booking['Tourist_Spot_Name'] = tourists_booking['Tourist_Spot_Name'].str.replace(r'^\d+\.\s', '', regex=True)
tourists_booking['Tourist_Spot_Category'] = tourists_booking['Tourist_Spot_Category'].astype(str)
tourists_booking['Tourist_Spot_Category'] = tourists_booking['Tourist_Spot_Category'].str.replace("•", "&")
tourists_booking['Tourist_Spot_Name'] = tourists_booking['Tourist_Spot_Name'].str.replace("ñ", "n")

In [10]:
tourists_booking['Tourist_Spot_Name'].unique()

array(['White Beach', 'Puerto Princesa Underground River', 'Intramuros',
       'Kayangan Lake', 'Nacpan Beach',
       'Chocolate Hills Natural Monument',
       'Yapak Beach (Puka Shell Beach)', 'Banaue Rice Terraces',
       'Big Lagoon', 'Fort Santiago', 'Basilica del Santo Nino',
       'Kawasan Falls', 'Greenbelt Mall', 'Ayala Center Cebu',
       'San Agustin Church', 'Rizal Park', 'Mayon Volcano',
       'Casa Gorordo Museum', 'Small Lagoon', 'Twin Lagoon',
       'Batad Rice Terraces', 'Tumalog Falls', 'Manila Ocean Park',
       'Barracuda Lake', 'Cambugahay Falls', 'Honda Bay', "Ariel's Point",
       'Taal Volcano', 'Fort San Pedro', 'Calle Crisologo'], dtype=object)

In [11]:
tourists_booking.to_csv('C:/Users/mneme/Desktop/Python Data Engineering files/Tourist_site.csv', header=True, index=False)